## Import modules

The following is needed to add the parent directory to the `PYTHONPATH`, so that the `thermo_flux` package can be imported:

In [2]:
import sys
import os
sys.path.append(os.path.dirname(os.getcwd()))

Import the required modules from `thermo_flux`:

In [3]:
from thermo_flux.io import load_excel as ex
from thermo_flux.io import load_gams as gm
from thermo_flux.io import load_sbml as sb
from thermo_flux.io import output as out
from thermo_flux.core import model

Note that you need to have `equilibrator-api` installed. If you are using Anaconda and have installed the package in a separate environment, do not forget to *activate* the environment before opening Jupyter Notebook.

## a. Starting from the original *excel* model 

In this section we need to provide two files as input:
- `model_excel`: a `.xlsx` file describing all the reactions and metabolites in the model. This should follow the template used by the MSB group.
- `keggids_csv`: a `.csv` file with the KEGG IDs of the metabolites in the model.

Additionally, if we want to manually edit some metabolites, we may do so by providing a *dictionary* via the input argument `edit_mets`. This specifies which metabolite fields will be altered (charge, formula, ...)

### a.1. Case 1: Yeast

In [3]:
tmodel_excel_yeast = ex.create_thermo_model("yeast", 
                                            model_excel="yeast\yeast_v3.SV_ENS_03.xlsx", 
                                            keggids_csv="yeast\yeast_kegg_id.csv",
                                            edit_mets={"ficytc": {"charge": 3},
                                                       "focytc": {"charge": 2},
                                                       "ac": {"charge": -1, 
                                                              "formula": "C2H3O2"},
                                                             }
                                            )

Restricted license - for non-production use only - expires 2024-10-28
['Parameters', 'Metabolites', 'Exchange reactions', 'Reactions', 'DV-IDENTITY-0', 'Transmembrane reactions', 'Biomass Composition', 'log']


C:\Users\p290481\Anaconda3\envs\thermoflux\lib\site-packages\openpyxl\worksheet\_reader.py:312: UserWarning: Unknown extension is not supported and will be removed
  warn(msg)
C:\Users\p290481\Anaconda3\envs\thermoflux\lib\site-packages\openpyxl\worksheet\_reader.py:312: UserWarning: Conditional Formatting extension is not supported and will be removed
  warn(msg)
C:\Users\p290481\Anaconda3\envs\thermoflux\lib\site-packages\openpyxl\worksheet\_reader.py:312: UserWarning: Unknown extension is not supported and will be removed
  warn(msg)
C:\Users\p290481\Anaconda3\envs\thermoflux\lib\site-packages\openpyxl\worksheet\_reader.py:312: UserWarning: Conditional Formatting extension is not supported and will be removed
  warn(msg)


*** Reading data from Reactions ***
unknown metabolite 'asp-L[c]' created
unknown metabolite 'atp[c]' created
unknown metabolite 'gln-L[c]' created
unknown metabolite 'h2o[c]' created
unknown metabolite 'amp[c]' created
unknown metabolite 'asn-L[c]' created
unknown metabolite 'glu-L[c]' created
unknown metabolite 'ppi[c]' created
unknown metabolite '4pasp[c]' created
unknown metabolite 'adp[c]' created
unknown metabolite 'akg[c]' created
unknown metabolite 'oaa[c]' created
unknown metabolite 'akg[m]' created
unknown metabolite 'asp-L[m]' created
unknown metabolite 'glu-L[m]' created
unknown metabolite 'oaa[m]' created
unknown metabolite 'nadph[c]' created
unknown metabolite 'aspsa[c]' created
unknown metabolite 'nadp[c]' created
unknown metabolite 'pi[c]' created
unknown metabolite 'pyr[c]' created
unknown metabolite 'ala-L[c]' created
unknown metabolite 'pyr[m]' created
unknown metabolite 'ala-L[m]' created
unknown metabolite 'udpg[c]' created
unknown metabolite 'glycogen[c]' created


*** Reading data from Transmembrane reactions ***
unknown metabolite 'electron[m]' created
unknown metabolite 'h[m]' created
unknown metabolite 'electron[c]' created
unknown metabolite 'h[c]' created
unknown metabolite 'ficytc[c]' created
unknown metabolite 'focytc[c]' created
unknown metabolite 'o2[m]' created
unknown metabolite 'charge[c]' created
unknown metabolite 'charge[m]' created
*** Reading data from Parameters ***
*** Adding  extra biomass reactions ***
*** Updating metabolite information ***
proteins_c compound unknown!  assigned as nothing
lipids_c compound unknown!  assigned as nothing
polysacch_c compound unknown!  assigned as nothing
dna_c compound unknown!  assigned as nothing
rna_c compound unknown!  assigned as nothing
storage_c compound unknown!  assigned as nothing
biomass_c assigned as biomass
biomass_e assigned as biomass
*** Editing special metabolites ***
*** Removing electrons from the model ***


The code above returns an instance of `thermo_flux.ThermoModel`:

In [4]:
type(tmodel_excel_yeast)

thermo_flux.core.model.ThermoModel

The "Parameters" sheet of the input excel file is parsed into a *dictionary* and stored as a model attribute:

In [6]:
tmodel_excel_yeast._parameters

{'Temperature (K)': 303.15,
 'Nh(biomass) (mmol/gDW)': 67,
 'dfG0(biomass) (KJ/gDW)': -3.040530303030303,
 'pH': {'Extracellular [e]': 5, 'Cytosol [c]': 7, 'Mitochondria [m]': 7.4},
 'Ionic Strength (M)': {'Extracellular [e]': 0.2,
  'Cytosol [c]': 0.2,
  'Mitochondria [m]': 0.2},
 'Electrical membrane potential (V)': {'e|>|c ': -0.06, 'c|>|m': -0.16},
 'Default bounds for variables': False,
 'Fluxes (mmol/gDW/h)': {'min': -500, 'max': 500},
 'Concentration (mM)': {'min': 0.001, 'max': 10},
 'sigmac(J/K/gDW/h)': {'min': 0, 'max': 100},
 'Physical constants': False,
 'Gas constant [KJ/mol/K]': 0.008314,
 'Faraday constant [KC/mol]': 96.49,
 'Debye-Hückel constant A [M^(-1/2)]': 1.186,
 'Debye-Hückel constant B [M^(-1/2)]': 1.6}

The information contained in the attribute `_parameters` is used to populate the appropriate attributes, `pH`, `I`, `T`, `phi_dict`:

In [9]:
tmodel_excel_yeast.pH, tmodel_excel_yeast.I, tmodel_excel_yeast.T, tmodel_excel_yeast.phi

({'e': 5 <Unit('dimensionless')>,
  'c': 7 <Unit('dimensionless')>,
  'm': 7.4 <Unit('dimensionless')>},
 {'e': 0.2 <Unit('molar')>,
  'c': 0.2 <Unit('molar')>,
  'm': 0.2 <Unit('molar')>},
 303.15 <Unit('kelvin')>,
 {'ec': -0.06 <Unit('volt')>, 'cm': -0.16 <Unit('volt')>})

We can check that the KEGG IDs of some metabolites:

In [10]:
tmodel_excel_yeast.metabolites.get_by_id("atp_c").annotation

{'kegg': 'C00002'}

... or confirm that the metabolites we "manually" edited have the expected property values:

In [11]:
tmodel_excel_yeast.metabolites.get_by_id("ficytc_c").charge

3

In [12]:
tmodel_excel_yeast.metabolites.get_by_id("focytc_c").charge

2

In [13]:
tmodel_excel_yeast.metabolites.get_by_id("ac_c").formula

'C2H3O2'

When a metabolite does not have a corresponding KEGG ID in the provided `.csv` file, the identifier is set to "UNKNOWN", as is the case for proteins, lipids, and other macromolecules in this model:

In [14]:
tmodel_excel_yeast.metabolites.get_by_id("proteins_c").annotation

{'metanetx.chemical': 'UNKNOWN'}

The biomass reaction is dealt with in a particular way. Even though there is no such metabolite as "biomass" in the model, we define it explicitly, to separate two processes: biomass production (in the cytosol) from the biomass exchange (system boundary).

(In the excel file, these reactions are lumped into one)

In [16]:
for r in tmodel_excel_yeast.reactions:
    if "biomass" in r.id:
        print(r)

biomass_c: dna_c + lipids_c + polysacch_c + proteins_c + rna_c + storage_c <=> biomass_c
biomass_ce: biomass_c <=> biomass_e
biomass_EX: biomass_e <=> 


To call equilibrator for the estimation of the $\Delta_fG^0$ values, we also need to provide the values of pMg. Since these were not defined in the `.xlsx` file, we provide them directly to the model via a dictionary:

In [17]:
from equilibrator_api import ComponentContribution, Q_

tmodel_excel_yeast.pMg = {"c": Q_(1, ''), 
                          "m": Q_(1, ''),
                          "e": Q_(1, '')}

Call eQuilibrator to update the thermodynamic information of the model:

In [18]:
tmodel_excel_yeast.update_thermo_info()

Identifying compounds...
Initilizing component contribution object.../229
[████████████████████████████████████████] 229/229

Estimating dfG0'...
[████████████████████████████████████████] 232/232

Estimating drG0'...
[████████████████████████████████████████] 289/289



Check some values:

In [19]:
tmodel_excel_yeast.metabolites[0].dfG0, tmodel_excel_yeast.metabolites[0].dfG_SE, tmodel_excel_yeast.metabolites[0].annotation

(-697.9611139718606 <Unit('kilojoule / mole')>,
 1.272536595863435 <Unit('kilojoule / mole')>,
 {'kegg': 'C00049'})

In [21]:
tmodel_excel_yeast.reactions[0].drG0

52.07649473101105 <Unit('kilojoule / mole')>

### a.2. Case 2: E. coli

Same as above, using a different model as the starting point:

In [22]:
tmodel_excel_ecoli = ex.create_thermo_model("ecoli", 
                                            model_excel="ecoli\model.xlsx", 
                                            keggids_csv="ecoli\ecoli_kegg_id.csv",
                                            edit_mets={"ac": {"charge": -1, 
                                                       "formula": "C2H3O2"},
                                                       }
                                            )

['Parameters', 'Exchange reactions', 'Reactions', 'Biomass Composition', 'Transmembrane reactions', 'Metabolites', 'references', 'Transmembrane_reactions_reed', 'Transmembrane reactions_Orth', 'Transmembrane reactions old', 'Sheet3', 'log', 'subsystems']
*** Reading data from Reactions ***
unknown metabolite '2dhglcn[c]' created
unknown metabolite 'nadh[c]' created
unknown metabolite 'glcn[c]' created
unknown metabolite 'nad[c]' created
unknown metabolite 'nadph[c]' created
unknown metabolite 'nadp[c]' created
unknown metabolite '2dhguln[c]' created
unknown metabolite 'idon-L[c]' created
unknown metabolite '3hcinnm[c]' created
unknown metabolite 'o2[c]' created
unknown metabolite 'dhcinnm[c]' created
unknown metabolite 'h2o[c]' created
unknown metabolite '3hpppn[c]' created
unknown metabolite 'dhpppn[c]' created
unknown metabolite 'phthr[c]' created
unknown metabolite '4hthr[c]' created
unknown metabolite 'pi[c]' created
unknown metabolite '5dglcn[c]' created
unknown metabolite 'ru5p-D

unknown metabolite '23doguln[c]' created
unknown metabolite '3dhguln[c]' created
unknown metabolite 'dpcoa[c]' created
unknown metabolite '2dhp[c]' created
unknown metabolite 'pant-R[c]' created
unknown metabolite '2dr5p[c]' created
unknown metabolite 'dtmp[c]' created
unknown metabolite 'dump[c]' created
unknown metabolite '2dr1p[c]' created
unknown metabolite 'dxyl5p[c]' created
unknown metabolite '2me4p[c]' created
unknown metabolite 'dxyl[c]' created
unknown metabolite '4per[c]' created
unknown metabolite 'ecaEC[c]' created
unknown metabolite 'udcpdp[c]' created
unknown metabolite '6pgc[c]' created
unknown metabolite 'kdo2lipid4[c]' created
unknown metabolite 'kdo2lipid4L[c]' created
unknown metabolite 'lipa[c]' created
unknown metabolite 'kdo2lipid4p[c]' created
unknown metabolite 'lipa_cold[c]' created
unknown metabolite '2pg[c]' created
unknown metabolite 'seramp[c]' created
unknown metabolite 'enter[c]' created
unknown metabolite 'etha[c]' created
unknown metabolite 'f6p[c]' cr

unknown metabolite 'pdx5p[c]' created
unknown metabolite 'pydxn[c]' created
unknown metabolite 'peamn[c]' created
unknown metabolite 'peEC[c]' created
unknown metabolite 'tagdp-D[c]' created
unknown metabolite '3php[c]' created
unknown metabolite '2pglyc[c]' created
unknown metabolite 'pgpEC[c]' created
unknown metabolite 'phe-L[c]' created
unknown metabolite 'phpyr[c]' created
unknown metabolite 'pcEC[c]' created
unknown metabolite '4r5au[c]' created
unknown metabolite '2mahmp[c]' created
unknown metabolite '4ppan[c]' created
unknown metabolite 'ppap[c]' created
unknown metabolite '4ppcys[c]' created
unknown metabolite 'pan4p[c]' created
unknown metabolite 'r1p[c]' created
unknown metabolite '34hpp[c]' created
unknown metabolite 'pppn[c]' created
unknown metabolite 'uaagmda[c]' created
unknown metabolite 'peptidoEC[c]' created
unknown metabolite 'fpram[c]' created
unknown metabolite 'prbamp[c]' created
unknown metabolite 'prfp[c]' created
unknown metabolite 'skm5p[c]' created
unknown 

unknown metabolite 'no3[c]' created
unknown metabolite 'sbt-D[c]' created
unknown metabolite 'sucr[c]' created
*** Reading data from Parameters ***
*** Adding  extra biomass reactions ***
*** Updating metabolite information ***
biomass_c assigned as biomass
biomass_e assigned as biomass
*** Editing special metabolites ***
*** Removing electrons from the model ***


In [23]:
tmodel_excel_ecoli._parameters

{'Temperature [K]': 310.15,
 'Nh(biomass) [mmol gCDW-1]': 74,
 'dfG0(biomass) [kJ gCDW-1]': -2.6922348484848486,
 'pH': {'extracellular [e]': 7, 'cytosol [c]': 7.6},
 'Ionic Strength (M)': {'extracellular [e]': 0.2, 'cytosol [c]': 0.15},
 'electrical membrane potential [V]': {'c|>|e': -0.15},
 'DEFAULT BOUNDS FOR VARIABLES': False,
 'concentration [mM]': {'min': 0.0001, 'max': 1},
 'gbmo [kJ gCDW-1 h-1]': {'min': False, 'max': False},
 'PHYSICAL CONSTANTS': False,
 'Gas constant [kJ mol-1 K-1]': 0.008314,
 'Faraday constant [kC mol-1]': 96.49,
 'Debye-Hückel constant A [M-1/2]': 1.201,
 'Debye-Hückel constant B [M-1/2]': 1.6}

In [24]:
tmodel_excel_ecoli.pMg = {"c": Q_(1, ''), 
                          "e": Q_(1, '')}

In [25]:
tmodel_excel_ecoli.update_thermo_info()

Identifying compounds...
Initilizing component contribution object.../772
[████████████████████████████████████████] 772/772

Estimating dfG0'...
[████████████████████████████████████████] 774/774

Estimating drG0'...


W:\Scripts\thermo_flux\thermo_flux\core\model.py:136: UserWarning: CYTBD is not balanced and could not be automatically balanced, please check reaction stoichiometry
  drg_transport, dg_protons, dg_electrostatic = drg_tools.calc_drGtransport(rxn)
W:\Scripts\thermo_flux\thermo_flux\core\model.py:136: UserWarning: CYTBO3 is not balanced and could not be automatically balanced, please check reaction stoichiometry
  drg_transport, dg_protons, dg_electrostatic = drg_tools.calc_drGtransport(rxn)


W:\Scripts\thermo_flux\thermo_flux\core\model.py:136: UserWarning: DMSOR1e is not balanced and could not be automatically balanced, please check reaction stoichiometry
  drg_transport, dg_protons, dg_electrostatic = drg_tools.calc_drGtransport(rxn)


W:\Scripts\thermo_flux\thermo_flux\core\model.py:136: UserWarning: DMSOR2e is not balanced and could not be automatically balanced, please check reaction stoichiometry
  drg_transport, dg_protons, dg_electrostatic = drg_tools.calc_drGtransport(rxn)


W:\Scripts\thermo_flux\thermo_flux\core\model.py:136: UserWarning: FDH2 is not balanced and could not be automatically balanced, please check reaction stoichiometry
  drg_transport, dg_protons, dg_electrostatic = drg_tools.calc_drGtransport(rxn)


...

W:\Scripts\thermo_flux\thermo_flux\core\model.py:136: UserWarning: NADH8 is not balanced and could not be automatically balanced, please check reaction stoichiometry
  drg_transport, dg_protons, dg_electrostatic = drg_tools.calc_drGtransport(rxn)


W:\Scripts\thermo_flux\thermo_flux\core\model.py:136: UserWarning: NO3R1 is not balanced and could not be automatically balanced, please check reaction stoichiometry
  drg_transport, dg_protons, dg_electrostatic = drg_tools.calc_drGtransport(rxn)
W:\Scripts\thermo_flux\thermo_flux\core\model.py:136: UserWarning: NO3R2 is not balanced and could not be automatically balanced, please check reaction stoichiometry
  drg_transport, dg_protons, dg_electrostatic = drg_tools.calc_drGtransport(rxn)


W:\Scripts\thermo_flux\thermo_flux\core\model.py:136: UserWarning: PIabc is not balanced and could not be automatically balanced, please check reaction stoichiometry
  drg_transport, dg_protons, dg_electrostatic = drg_tools.calc_drGtransport(rxn)


W:\Scripts\thermo_flux\thermo_flux\core\model.py:136: UserWarning: TMAOR1e is not balanced and could not be automatically balanced, please check reaction stoichiometry
  drg_transport, dg_protons, dg_electrostatic = drg_tools.calc_drGtransport(rxn)
W:\Scripts\thermo_flux\thermo_flux\core\model.py:136: UserWarning: TMAOR2e is not balanced and could not be automatically balanced, please check reaction stoichiometry
  drg_transport, dg_protons, dg_electrostatic = drg_tools.calc_drGtransport(rxn)


[████████████████████████████████████████] 1064/1064



In [26]:
tmodel_excel_ecoli.metabolites[0].dfG0, tmodel_excel_ecoli.metabolites[0].dfG_SE, tmodel_excel_ecoli.metabolites[0].annotation

(0.0 <Unit('kilojoule / mole')>,
 3000.0 <Unit('kilojoule / mole')>,
 {'kegg': 'C95000'})

In [28]:
tmodel_excel_ecoli.reactions[0].drG0

-1153.1063820643355 <Unit('kilojoule / mole')>

## b. Starting from the GAMS-generated model [limited applicability]

In this section we need to provide two files as input:
- `model_excel`: a `.xlsx` file describing all the reactions and metabolites in the model.
- `keggids_csv`: a `.csv` file with the KEGG IDs of the metabolites in the model.

And, optionally:
- `regr_excel`: a `.xlsx` with the results of a *regression* performed in GAMS
- `va_excel`: a `.xlsx` with the results of a *variability analysis* performed in GAMS
- `edit_mets`: a *dictionary* for altering the fields of specified metabolites (charge, formula, ...). See example above.
- `**kwargs_rxns`

**Note:** all three `.xlsx` files described above were originally obtained from GAMS (`.gdx` format). For the format conversion, one needs to perform the following steps:
1. Open the GAMS terminal: GAMS Studio > Tools > Terminal
2. Change to the appropriate direcory: `cd path/to/dir`
3. Run: `for /f %f in ('dir /b ') do gdx2xls %f`

### b.1. Case 1: Yeast

In [36]:
tmodel_gams_yeast = gm.create_thermo_model_from_gams("yeast", 
                                                     model_excel="yeast\\model_yeast_from-GAMS.xlsx", 
                                                     keggids_csv="yeast\\yeast_kegg_id.csv",
                                                     regr_excel="yeast\\yeast_regdata_from-GAMS.xlsx",  # optional 
                                                     va_excel="yeast\\yeast_vabounds_from-GAMS.xlsx",  # optional
                                                     )

*** Building model from stoichiometrix matrix ***
*** Adding  extra biomass reactions ***
*** Updating metabolite information ***
dna compound unknown!  assigned as nothing
lipids compound unknown!  assigned as nothing
polysacch compound unknown!  assigned as nothing
proteins compound unknown!  assigned as nothing
rna compound unknown!  assigned as nothing
storage compound unknown!  assigned as nothing
biomass assigned as biomass
biomass assigned as biomass
*** Editing special metabolites ***
... no drGerror values added.
Provided V.A. data does not contain 'dfGLimits'...
Provided V.A. data does not contain 'FluxLimits'...


In [30]:
type(tmodel_gams_yeast)

thermo_flux.core.model.ThermoModel

The **scalar parameters** from the model are stored in one of the model attributes as a *dictionary*:

In [31]:
tmodel_gams_yeast._parameters

{'CI': 2.95, 'epsilon': 0.5, 'GasCons': 0.008314, 'Temp': 303.15}

The **nullspace matrix** is also stored in a model attribute:

In [32]:
tmodel_gams_yeast._nullspace

nsID     ns1  ns10  ns11  ns12  ns13  ns14  ns15  ns16  ns17  ns18  ...  ns32  \
rxns                                                                ...         
ACOAH    NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  ...   NaN   
ACONT    NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  ...   NaN   
ACONTm   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  ...   NaN   
ACS      NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  ...   NaN   
ACSm     NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  ...   NaN   
...      ...   ...   ...   ...   ...   ...   ...   ...   ...   ...  ...   ...   
ampSYN1  NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  ...   NaN   
ampSYN2  NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  ...   NaN   
fum      NaN   NaN   NaN   NaN   NaN   NaN  -1.0   NaN   NaN   NaN  ...   NaN   
gmpSYN1  NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  ...   NaN   
gmpSYN2  NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  ...   NaN   

nsID     ns33  ns38  ns39  ns4  ns5  ns6  ns7  ns8  ns9  
rxns                                                     
ACOAH     NaN   NaN   NaN  NaN  NaN  NaN  NaN  NaN  NaN  
ACONT     NaN   NaN   NaN -1.0  NaN  NaN  NaN  NaN  NaN  
ACONTm    NaN   NaN   NaN  1.0  NaN  NaN  NaN  NaN  NaN  
ACS       NaN   NaN   NaN  NaN  NaN  NaN  NaN  NaN  NaN  
ACSm      NaN   NaN   NaN  NaN  NaN  NaN  NaN  NaN  NaN  
...       ...   ...   ...  ...  ...  ...  ...  ...  ...  
ampSYN1   NaN   NaN   NaN  NaN  NaN  NaN  NaN  NaN  NaN  
ampSYN2   NaN   NaN   NaN  NaN  NaN  NaN  NaN  NaN  NaN  
fum       NaN   NaN   NaN  NaN  NaN  NaN  NaN  NaN  NaN  
gmpSYN1   NaN   NaN   NaN  NaN  NaN  NaN  NaN  NaN  NaN  
gmpSYN2   NaN   NaN   NaN  NaN  NaN  NaN  NaN  NaN  NaN  

[98 rows x 35 columns]

The upper and lower **flux bounds** for the fluxes are also stored:

In [33]:
tmodel_gams_yeast.fluxLimits

dim2               v_lo        v_up
dim1                               
2OBUTtm-1        -500.0  500.000000
2OBUTtm-1+H      -500.0  500.000000
2OXOADPAKGtm-2-2    0.0   29.676483
3MOBtm-1         -500.0  500.000000
3MOBtm-1+H       -500.0  500.000000
...                 ...         ...
storage_EX       -500.0  290.248497
storage_reaction -500.0  290.248497
succ_EX          -500.0  500.000000
umpSYN              0.0   55.300000
zymstSYN            0.0    1.100000

[286 rows x 2 columns]

**IMPORTANT:** the values might be conflicting with the default values with each the instances of `ThermoReaction` were initialized  (i.e. the values specified by `**kwargs_rxn` above)

In [34]:
# Values stored in the attribute model.fluxLimits
tmodel_gams_yeast.fluxLimits.loc["CS"]

dim2
v_lo      0.0
v_up    500.0
Name: CS, dtype: float64

In [35]:
# Default values stored in the instance of ThermoReaction:
tmodel_gams_yeast.reactions.get_by_id("CS").bounds

(-500, 500)

The **thermodynamic information** from the *regression* and *variability analysis* files is stored as a dataframe in one of the model attributes:

In [37]:
tmodel_gams_yeast._thermo

drG0         drGSE  drGerror      drG_lo      drG_up  \
dim1                                                                     
fum          -3.440000      0.282179       NaN  -27.486070   20.606070   
histd        -9.724960      2.226012       NaN  -74.325799    8.448597   
ASNS1       -30.993729      3.706250       NaN -151.926413   33.917401   
ASPK         19.099069      2.973315       NaN  -38.868425   56.887400   
ASPTA         2.870000      0.551284       NaN  -47.952502   42.545203   
...                ...           ...       ...         ...         ...   
proteins_EX   0.000000           NaN       NaN         NaN         NaN   
dna_EX        0.000000           NaN       NaN         NaN         NaN   
rna_EX        0.000000           NaN       NaN         NaN         NaN   
biomass       0.000000  10000.000000       NaN -266.522391 -266.522391   
biomass_EX    0.000000           NaN       NaN         NaN         NaN   

             va_drG_lo  va_drG_up  
dim1                               
fum          -1.834476   1.584916  
histd       -48.427255 -17.723574  
ASNS1       -79.008726 -63.430520  
ASPK         -7.503781  -0.500000  
ASPTA       -13.924800   1.849807  
...                ...        ...  
proteins_EX        NaN        NaN  
dna_EX             NaN        NaN  
rna_EX             NaN        NaN  
biomass            NaN        NaN  
biomass_EX         NaN        NaN  

[288 rows x 7 columns]

The `.gdx` read does not contain the values of pH, pMg or ionic strength. These will be passed directly to the instance of `ThermoModel`:

In [39]:
tmodel_gams_yeast.pMg = {"c": Q_(1, ''),  # unitless
                         "m": Q_(1, ''), 
                         "e": Q_(1, '')}

tmodel_gams_yeast.pH = {"c": Q_(7, ''),  # unitless 
                        "m": Q_(7, ''), 
                        "e": Q_(7, '')}

tmodel_gams_yeast.I =  {"c": Q_(0.1, 'M'), 
                        "m": Q_(0.1, 'M'), 
                        "e": Q_(0.1, 'M')}

tmodel_gams_yeast.T = Q_(303, 'K')

In [40]:
tmodel_gams_yeast.update_thermo_info()

Identifying compounds...
Initilizing component contribution object.../229
[████████████████████████████████████████] 229/229

Estimating dfG0'...
[████████████████████████████████████████] 232/232

Estimating drG0'...


W:\Scripts\thermo_flux\thermo_flux\core\model.py:136: UserWarning: ACt-1+H is not balanced and could not be automatically balanced, please check reaction stoichiometry
  drg_transport, dg_protons, dg_electrostatic = drg_tools.calc_drGtransport(rxn)


W:\Scripts\thermo_flux\thermo_flux\core\model.py:136: UserWarning: ATPASE is not balanced and could not be automatically balanced, please check reaction stoichiometry
  drg_transport, dg_protons, dg_electrostatic = drg_tools.calc_drGtransport(rxn)
W:\Scripts\thermo_flux\thermo_flux\core\model.py:136: UserWarning: ATPS3m is not balanced and could not be automatically balanced, please check reaction stoichiometry
  drg_transport, dg_protons, dg_electrostatic = drg_tools.calc_drGtransport(rxn)


W:\Scripts\thermo_flux\thermo_flux\core\model.py:136: UserWarning: CO2t-1+H is not balanced and could not be automatically balanced, please check reaction stoichiometry
  drg_transport, dg_protons, dg_electrostatic = drg_tools.calc_drGtransport(rxn)


W:\Scripts\thermo_flux\thermo_flux\core\model.py:136: UserWarning: ComplexIII is not balanced and could not be automatically balanced, please check reaction stoichiometry
  drg_transport, dg_protons, dg_electrostatic = drg_tools.calc_drGtransport(rxn)
W:\Scripts\thermo_flux\thermo_flux\core\model.py:136: UserWarning: ComplexIV is not balanced and could not be automatically balanced, please check reaction stoichiometry
  drg_transport, dg_protons, dg_electrostatic = drg_tools.calc_drGtransport(rxn)


W:\Scripts\thermo_flux\thermo_flux\core\model.py:136: UserWarning: PIt-1+H is not balanced and could not be automatically balanced, please check reaction stoichiometry
  drg_transport, dg_protons, dg_electrostatic = drg_tools.calc_drGtransport(rxn)
W:\Scripts\thermo_flux\thermo_flux\core\model.py:136: UserWarning: PItm-2+2H is not balanced and could not be automatically balanced, please check reaction stoichiometry
  drg_transport, dg_protons, dg_electrostatic = drg_tools.calc_drGtransport(rxn)
W:\Scripts\thermo_flux\thermo_flux\core\model.py:136: UserWarning: PItm-2+H is not balanced and could not be automatically balanced, please check reaction stoichiometry
  drg_transport, dg_protons, dg_electrostatic = drg_tools.calc_drGtransport(rxn)


W:\Scripts\thermo_flux\thermo_flux\core\model.py:136: UserWarning: SUCCt-2+2H is not balanced and could not be automatically balanced, please check reaction stoichiometry
  drg_transport, dg_protons, dg_electrostatic = drg_tools.calc_drGtransport(rxn)
W:\Scripts\thermo_flux\thermo_flux\core\model.py:136: UserWarning: SUCCt-2+H is not balanced and could not be automatically balanced, please check reaction stoichiometry
  drg_transport, dg_protons, dg_electrostatic = drg_tools.calc_drGtransport(rxn)


[████████████████████████████████████████] 289/289



In [41]:
tmodel_gams_yeast.metabolites[0].dfG0, tmodel_gams_yeast.metabolites[0].dfG_SE, tmodel_gams_yeast.metabolites[0].annotation

(-469.66340232395584 <Unit('kilojoule / mole')>,
 3.4299738752265516 <Unit('kilojoule / mole')>,
 {'kegg': 'C00109'})

### b.2. Case 2: E. coli

In [52]:
tmodel_gams_ecoli = gm.create_thermo_model_from_gams("ecoli", 
                                                     model_excel="ecoli\\model_ecoli_from-GAMS.xlsx", 
                                                     keggids_csv="ecoli\\ecoli_kegg_id.csv",
                                                     regr_excel="ecoli\\ecoli_regdata_from-GAMS.xlsx",  # optional 
                                                     va_excel="ecoli\\ecoli_vabounds_from-GAMS.xlsx",  # optional
                                                    )

*** Building model from stoichiometrix matrix ***
*** Adding  extra biomass reactions ***
*** Updating metabolite information ***
biomass assigned as biomass
biomass assigned as biomass
*** Editing special metabolites ***
Provided regression data does not have a sheet called 'dfG_bmm'
Provided regression data does not contain 'drGerror'...
... no drGerror values added.
Provided V.A. data does not contain 'dfGLimits'...
Provided V.A. data does not contain 'FluxLimits'...


In [53]:
tmodel_gams_ecoli._parameters

{'CI': 1.96, 'epsilon': 0.5, 'GasCons': 0.008314, 'Temp': 310.15}

In [54]:
tmodel_gams_ecoli._nullspace

nsID      ns1  ns10  ns100  ns101  ns102  ns103  ns104  ns105  ns106  ns107  \
rxns                                                                          
2DGLCNRx  1.0   NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
2DGLCNRy -1.0   NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
2DGULRx  -1.0   NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
2DGULRy   1.0   NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
AACPS1    NaN   NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
...       ...   ...    ...    ...    ...    ...    ...    ...    ...    ...   
XYLI2i    NaN   NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
XYLabc    NaN   NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
cytd      NaN   NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
fum       NaN   NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
ppa       NaN   NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   

nsID      ...  ns90  ns91  ns92  ns93  ns94  ns95  ns96  ns97  ns98  ns99  
rxns      ...                                                              
2DGLCNRx  ...   NaN   NaN   NaN  -1.0   NaN   NaN   NaN   1.0   NaN   NaN  
2DGLCNRy  ...   NaN   NaN   NaN   1.0   NaN   NaN   NaN  -1.0   NaN   NaN  
2DGULRx   ...   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  
2DGULRy   ...   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  
AACPS1    ...   NaN   NaN   NaN   NaN  0.04   NaN   NaN   NaN   NaN   NaN  
...       ...   ...   ...   ...   ...   ...   ...   ...   ...   ...   ...  
XYLI2i    ...   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  
XYLabc    ...   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  
cytd      ...   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  
fum       ...   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  
ppa       ...   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  

[435 rows x 210 columns]

In [55]:
tmodel_gams_ecoli._stoichmatrix

mets      10fthf_c  12dgrEC_c  12ppd-S_c  12ppd-S_e  13dpg_c  15dap_c  \
rxns                                                                    
12PPDt         NaN        NaN        1.0       -1.0      NaN      NaN   
2DGLCNRx       NaN        NaN        NaN        NaN      NaN      NaN   
2DGLCNRy       NaN        NaN        NaN        NaN      NaN      NaN   
2DGULRx        NaN        NaN        NaN        NaN      NaN      NaN   
2DGULRy        NaN        NaN        NaN        NaN      NaN      NaN   
...            ...        ...        ...        ...      ...      ...   
fum            NaN        NaN        NaN        NaN      NaN      NaN   
glucys         NaN        NaN        NaN        NaN      NaN      NaN   
histd          NaN        NaN        NaN        NaN      NaN      NaN   
ppa            NaN        NaN        NaN        NaN      NaN      NaN   
udcpdp         NaN        NaN        NaN        NaN      NaN      NaN   

mets      15dap_e  1pyr5c_c  23ddhb_c  23dhb_c  ...  xan_c  xan_e  xmp_c  \
rxns                                            ...                        
12PPDt        NaN       NaN       NaN      NaN  ...    NaN    NaN    NaN   
2DGLCNRx      NaN       NaN       NaN      NaN  ...    NaN    NaN    NaN   
2DGLCNRy      NaN       NaN       NaN      NaN  ...    NaN    NaN    NaN   
2DGULRx       NaN       NaN       NaN      NaN  ...    NaN    NaN    NaN   
2DGULRy       NaN       NaN       NaN      NaN  ...    NaN    NaN    NaN   
...           ...       ...       ...      ...  ...    ...    ...    ...   
fum           NaN       NaN       NaN      NaN  ...    NaN    NaN    NaN   
glucys        NaN       NaN       NaN      NaN  ...    NaN    NaN    NaN   
histd         NaN       NaN       NaN      NaN  ...    NaN    NaN    NaN   
ppa           NaN       NaN       NaN      NaN  ...    NaN    NaN    NaN   
udcpdp        NaN       NaN       NaN      NaN  ...    NaN    NaN    NaN   

mets      xtsn_c  xtsn_e  xu5p-D_c  xu5p-L_c  xyl-D_c  xyl-D_e  xylu-D_c  
rxns                                                                      
12PPDt       NaN     NaN       NaN       NaN      NaN      NaN       NaN  
2DGLCNRx     NaN     NaN       NaN       NaN      NaN      NaN       NaN  
2DGLCNRy     NaN     NaN       NaN       NaN      NaN      NaN       NaN  
2DGULRx      NaN     NaN       NaN       NaN      NaN      NaN       NaN  
2DGULRy      NaN     NaN       NaN       NaN      NaN      NaN       NaN  
...          ...     ...       ...       ...      ...      ...       ...  
fum          NaN     NaN       NaN       NaN      NaN      NaN       NaN  
glucys       NaN     NaN       NaN       NaN      NaN      NaN       NaN  
histd        NaN     NaN       NaN       NaN      NaN      NaN       NaN  
ppa          NaN     NaN       NaN       NaN      NaN      NaN       NaN  
udcpdp       NaN     NaN       NaN       NaN      NaN      NaN       NaN  

[1062 rows x 763 columns]

In [56]:
tmodel_gams_ecoli._thermo

drG0        drGSE  drGerror      drG_lo      drG_up  \
dim1                                                                    
alltn       -59.581899     9.554346       NaN -102.058082  -17.105716   
cytd        -14.359996     1.123807       NaN  -55.648289  -11.643626   
fum          -3.440000     0.282179       NaN  -34.179107   28.979626   
glucys      -33.387509     5.522529       NaN  -98.119836   34.576155   
histd       -19.095138     2.226012       NaN -106.044949   60.639695   
...                ...          ...       ...         ...         ...   
EX_xan       53.506881          NaN       NaN   11.944967   35.694632   
EX_xtsn    -110.059358          NaN       NaN -151.621272 -127.871607   
EX_xyl-D   -326.557798          NaN       NaN -368.119712 -344.370047   
biomass       0.000000  1000.000000       NaN  701.767161  701.767161   
biomass_EX    0.000000          NaN       NaN         NaN         NaN   

             va_drG_lo  va_drG_up  
dim1                               
alltn              NaN        NaN  
cytd        -49.811345 -13.974016  
fum         -11.152436  -0.500000  
glucys             NaN        NaN  
histd       -55.204732  -1.013127  
...                ...        ...  
EX_xan             NaN        NaN  
EX_xtsn            NaN        NaN  
EX_xyl-D           NaN        NaN  
biomass    -264.962325 -77.810143  
biomass_EX         NaN        NaN  

[1063 rows x 7 columns]

By default, `ThermoModel` is initialized with specific values of Temperature, ionic strength, pH, etc.
We can manually set them to fit our model:

In [58]:
tmodel_gams_ecoli.pMg = {"c": Q_(1, ''),  # unitless
                         "e": Q_(1, '')}

tmodel_gams_ecoli.pH = {"c": Q_(7, ''),  # unitless 
                        "e": Q_(7, '')}

tmodel_gams_ecoli.I =  {"c": Q_(0.1, 'M'), 
                        "e": Q_(0.1, 'M')}

tmodel_gams_ecoli.T = Q_(310.15, 'K')

And now we can call eQuilibrator to estimate the standard Gibbs energies:

In [59]:
tmodel_gams_ecoli.update_thermo_info()

Identifying compounds...
Initilizing component contribution object.../765
[████████████████████████████████████████] 765/765

Estimating dfG0'...
[████████████████████████████████████████] 767/767

Estimating drG0'...


W:\Scripts\thermo_flux\thermo_flux\core\model.py:136: UserWarning: ATPS4r is not balanced and could not be automatically balanced, please check reaction stoichiometry
  drg_transport, dg_protons, dg_electrostatic = drg_tools.calc_drGtransport(rxn)


W:\Scripts\thermo_flux\thermo_flux\core\model.py:136: UserWarning: CSNt2 is not balanced and could not be automatically balanced, please check reaction stoichiometry
  drg_transport, dg_protons, dg_electrostatic = drg_tools.calc_drGtransport(rxn)
W:\Scripts\thermo_flux\thermo_flux\core\model.py:136: UserWarning: CSNt2_add is not balanced and could not be automatically balanced, please check reaction stoichiometry
  drg_transport, dg_protons, dg_electrostatic = drg_tools.calc_drGtransport(rxn)


W:\Scripts\thermo_flux\thermo_flux\core\model.py:136: UserWarning: CYTBD is not balanced and could not be automatically balanced, please check reaction stoichiometry
  drg_transport, dg_protons, dg_electrostatic = drg_tools.calc_drGtransport(rxn)
W:\Scripts\thermo_flux\thermo_flux\core\model.py:136: UserWarning: CYTBO3 is not balanced and could not be automatically balanced, please check reaction stoichiometry
  drg_transport, dg_protons, dg_electrostatic = drg_tools.calc_drGtransport(rxn)


W:\Scripts\thermo_flux\thermo_flux\core\model.py:136: UserWarning: DMSOR1e is not balanced and could not be automatically balanced, please check reaction stoichiometry
  drg_transport, dg_protons, dg_electrostatic = drg_tools.calc_drGtransport(rxn)
W:\Scripts\thermo_flux\thermo_flux\core\model.py:136: UserWarning: DMSOR2e is not balanced and could not be automatically balanced, please check reaction stoichiometry
  drg_transport, dg_protons, dg_electrostatic = drg_tools.calc_drGtransport(rxn)


...

W:\Scripts\thermo_flux\thermo_flux\core\model.py:136: UserWarning: THMDt2 is not balanced and could not be automatically balanced, please check reaction stoichiometry
  drg_transport, dg_protons, dg_electrostatic = drg_tools.calc_drGtransport(rxn)
W:\Scripts\thermo_flux\thermo_flux\core\model.py:136: UserWarning: THMDt2_add is not balanced and could not be automatically balanced, please check reaction stoichiometry
  drg_transport, dg_protons, dg_electrostatic = drg_tools.calc_drGtransport(rxn)
W:\Scripts\thermo_flux\thermo_flux\core\model.py:136: UserWarning: THMabc is not balanced and could not be automatically balanced, please check reaction stoichiometry
  drg_transport, dg_protons, dg_electrostatic = drg_tools.calc_drGtransport(rxn)


W:\Scripts\thermo_flux\thermo_flux\core\model.py:136: UserWarning: THRt4 is not balanced and could not be automatically balanced, please check reaction stoichiometry
  drg_transport, dg_protons, dg_electrostatic = drg_tools.calc_drGtransport(rxn)
W:\Scripts\thermo_flux\thermo_flux\core\model.py:136: UserWarning: TMAOR1e is not balanced and could not be automatically balanced, please check reaction stoichiometry
  drg_transport, dg_protons, dg_electrostatic = drg_tools.calc_drGtransport(rxn)


W:\Scripts\thermo_flux\thermo_flux\core\model.py:136: UserWarning: TMAOR2e is not balanced and could not be automatically balanced, please check reaction stoichiometry
  drg_transport, dg_protons, dg_electrostatic = drg_tools.calc_drGtransport(rxn)


W:\Scripts\thermo_flux\thermo_flux\core\model.py:136: UserWarning: URIt2 is not balanced and could not be automatically balanced, please check reaction stoichiometry
  drg_transport, dg_protons, dg_electrostatic = drg_tools.calc_drGtransport(rxn)
W:\Scripts\thermo_flux\thermo_flux\core\model.py:136: UserWarning: URIt2_add is not balanced and could not be automatically balanced, please check reaction stoichiometry
  drg_transport, dg_protons, dg_electrostatic = drg_tools.calc_drGtransport(rxn)


[████████████████████████████████████████] 1064/1064



In [60]:
tmodel_gams_ecoli.metabolites[0].dfG0, tmodel_gams_ecoli.metabolites[0].dfG_SE, tmodel_gams_ecoli.metabolites[0].annotation

(-332.1939370390986 <Unit('kilojoule / mole')>,
 1.0129131754913412 <Unit('kilojoule / mole')>,
 {'kegg': 'C02917'})

In [61]:
tmodel_gams_ecoli.reactions[0].drG0

0.0 <Unit('kilojoule / mole')>

In [62]:
tmodel_gams_ecoli.dfG0_cov_sqrt   # covariance matrix

array([[ 3.01486986e-04,  6.52235949e-04,  5.97279956e-04, ...,
         0.00000000e+00,  0.00000000e+00,  0.00000000e+00],
       [ 3.01486986e-04,  6.52235949e-04,  5.97279956e-04, ...,
         0.00000000e+00,  0.00000000e+00,  0.00000000e+00],
       [ 0.00000000e+00,  0.00000000e+00,  0.00000000e+00, ...,
         0.00000000e+00,  0.00000000e+00,  0.00000000e+00],
       ...,
       [ 0.00000000e+00,  0.00000000e+00,  0.00000000e+00, ...,
         0.00000000e+00,  0.00000000e+00,  0.00000000e+00],
       [ 3.43083901e-18, -8.42534648e-18,  8.56258561e-18, ...,
         0.00000000e+00,  0.00000000e+00,  0.00000000e+00],
       [ 3.43083901e-18, -8.42534648e-18,  8.56258561e-18, ...,
         0.00000000e+00,  0.00000000e+00,  0.00000000e+00]]) <Unit('kilojoule / mole')>

## c. Exporting a model to `.sbml`

We need to provide:
- `model`: an instance of `ThermoModel`
- `sbml_filename`: the name of the `.sbml` that will contain the model

and, optionally, also a `hdf5_filename`. This will be used to generate a `.hdf5` file containing the data that does cannot be included in the traditional format `.sbml` (e.g. the covariance matrix). We need to specify which attributes are to be saved in the `.hdf5` file, by passing a list to the input argument `attrs_for_hdf5`:

**Note**: the current implementation does not support saving of `pd.DataFrame` (such as the `._nullspace` attribute after importing the models from GAMS). They first need to be converted to `np.array` with units:

In [73]:
tmodel_gams_yeast._nullspace = Q_(tmodel_gams_yeast._nullspace.to_numpy(), '')
tmodel_gams_yeast._nullspace

array([[nan, nan, nan, ..., nan, nan, nan],
       [nan, nan, nan, ..., nan, nan, nan],
       [nan, nan, nan, ..., nan, nan, nan],
       ...,
       [nan, nan, nan, ..., nan, nan, nan],
       [nan, nan, nan, ..., nan, nan, nan],
       [nan, nan, nan, ..., nan, nan, nan]]) <Unit('dimensionless')>

In [75]:
tmodel_gams_yeast.dfG0_cov_sqrt

array([[-1.50390117e-13,  0.00000000e+00,  0.00000000e+00, ...,
         0.00000000e+00,  0.00000000e+00,  0.00000000e+00],
       [-1.50390117e-13,  0.00000000e+00,  0.00000000e+00, ...,
         0.00000000e+00,  0.00000000e+00,  0.00000000e+00],
       [ 0.00000000e+00, -3.00000000e+03,  0.00000000e+00, ...,
         0.00000000e+00,  0.00000000e+00,  0.00000000e+00],
       ...,
       [ 3.04956211e-18,  0.00000000e+00,  0.00000000e+00, ...,
         0.00000000e+00,  0.00000000e+00,  0.00000000e+00],
       [ 3.04956211e-18,  0.00000000e+00,  0.00000000e+00, ...,
         0.00000000e+00,  0.00000000e+00,  0.00000000e+00],
       [ 3.04956211e-18,  0.00000000e+00,  0.00000000e+00, ...,
         0.00000000e+00,  0.00000000e+00,  0.00000000e+00]]) <Unit('kilojoule / mole')>

In [74]:
out.write_model(model=tmodel_gams_yeast, 
                sbml_filename="demo_io_gams.sbml",
                hdf5_filename="demo_io_gams.hdf5",
                attrs_for_hdf5=["dfG0_cov_sqrt", "_nullspace"]
               )

## d. Starting from a previously exported `.sbml` model

In [76]:
model_sbml_yeast = sb.load_model(sbml_filename="demo_io_gams.sbml", 
                                 hdf5_filename="demo_io_gams.hdf5",   # optional
                                 )

ERROR:cobra.io.sbml:No objective coefficients in model. Unclear what should be optimized


Attribute '_nullspace' not in the model. Loading values from .hdf5 file.
Attribute 'dfG0_cov_sqrt' not in the model. Loading values from .hdf5 file.
Initilizing component contribution object...
'ThermoReaction' object has no attribute 'transported'
'ThermoReaction' object has no attribute 'transported'
'ThermoReaction' object has no attribute 'transported'
'ThermoReaction' object has no attribute 'transported'
'ThermoReaction' object has no attribute 'transported'
'ThermoReaction' object has no attribute 'transported'
'ThermoReaction' object has no attribute 'transported'
'ThermoReaction' object has no attribute 'transported'
'ThermoReaction' object has no attribute 'transported'
'ThermoReaction' object has no attribute 'transported'
'ThermoReaction' object has no attribute 'transported'
'ThermoReaction' object has no attribute 'transported'
'ThermoReaction' object has no attribute 'transported'
'ThermoReaction' object has no attribute 'transported'
'ThermoReaction' object has no attri

In [77]:
type(model_sbml_yeast)

thermo_flux.core.model.ThermoModel

From the `.hdf5` file, we recover model-wide information which is stored in model attributes.

The attributes below would be *inexistent* if we had not specified `hdf5_filename` above.

In [78]:
model_sbml_yeast.dfG0_cov_sqrt

array([[-1.50390117e-13,  0.00000000e+00,  0.00000000e+00, ...,
         0.00000000e+00,  0.00000000e+00,  0.00000000e+00],
       [-1.50390117e-13,  0.00000000e+00,  0.00000000e+00, ...,
         0.00000000e+00,  0.00000000e+00,  0.00000000e+00],
       [ 0.00000000e+00, -3.00000000e+03,  0.00000000e+00, ...,
         0.00000000e+00,  0.00000000e+00,  0.00000000e+00],
       ...,
       [ 3.04956211e-18,  0.00000000e+00,  0.00000000e+00, ...,
         0.00000000e+00,  0.00000000e+00,  0.00000000e+00],
       [ 3.04956211e-18,  0.00000000e+00,  0.00000000e+00, ...,
         0.00000000e+00,  0.00000000e+00,  0.00000000e+00],
       [ 3.04956211e-18,  0.00000000e+00,  0.00000000e+00, ...,
         0.00000000e+00,  0.00000000e+00,  0.00000000e+00]]) <Unit('kilojoule / mole')>

In [81]:
model_sbml_yeast.__nullspace

array([[nan, nan, nan, ..., nan, nan, nan],
       [nan, nan, nan, ..., nan, nan, nan],
       [nan, nan, nan, ..., nan, nan, nan],
       ...,
       [nan, nan, nan, ..., nan, nan, nan],
       [nan, nan, nan, ..., nan, nan, nan],
       [nan, nan, nan, ..., nan, nan, nan]]) <Unit('dimensionless')>

From the `.sbml` file, we generate the model. Furthermore, the reactions and metabolites now contain thermodynamic, flux or concentration information, stored in the `notes` field.

In [82]:
model_sbml_yeast.reactions.get_by_id("CS").notes

{'drG0': '10.127532699765538 kilojoule / mole',
 'drG0prime': '-38.96434288662863 kilojoule / mole',
 'drGtransport': '0 kilojoule / mole',
 'drG_h_transport': '0 kilojoule / mole',
 'drG_c_transport': '0 kilojoule / mole',
 'drG_SE': '0.43731945413956436 kilojoule / mole',
 'balanced': 'False'}

In [83]:
model_sbml_yeast.metabolites.get_by_id("atp_c").notes

{'concentration': '1 molar',
 'lower_bound': '1 millimolar',
 'upper_bound': '1 molar',
 'accession': 'atp',
 'redox': 'False',
 'biomass': 'False',
 'dfG0': '-2811.578331958078 kilojoule / mole',
 'dfG0prime': '-2308.7678869716574 kilojoule / mole',
 'dfG_SE': '1.4899855434834732 kilojoule / mole'}